In [1]:
from __future__ import annotations

import random
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import seaborn as sns
import torch
import torch.nn as nn

from scipy.integrate import solve_ivp
from scipy.integrate import odeint

import scipy

import sys
import gymnasium as gym
import time
import signal

# 定义环境的相关设置
balance_time = 240
h_in = 1 / 100

# 注册和创建自定义环境
CartPoleSwingUp = gym.register(
    id = 'CartPoleSwingUp',
    entry_point = 'myCartpoleF_SwingUp:CartPoleSwingUp',  # 根据你的环境路径修改
    reward_threshold = -40 * 0.95,
    max_episode_steps = int(balance_time / h_in),
)
env = gym.make('CartPoleSwingUp', render_mode='human')
print(gym.spec('CartPoleSwingUp'))

EnvSpec(id='CartPoleSwingUp', entry_point='myCartpoleF_SwingUp:CartPoleSwingUp', reward_threshold=-38.0, nondeterministic=False, max_episode_steps=24000, order_enforce=True, disable_env_checker=False, kwargs={}, namespace=None, name='CartPoleSwingUp', version=None, additional_wrappers=(), vector_entry_point=None)


创建 NormalActionNoise 实例，用于在智能体的动作中加入噪声。具体的参数含义如下：

mean = np.zeros(env.action_space.shape): 这里的 mean 是噪声的均值，np.zeros(env.action_space.shape) 表示均值为零，且它的维度与环境的动作空间 env.action_space.shape 相同。env.action_space.shape 表示动作空间的维度。

sigma = 0.1 * np.ones(env.action_space.shape): 这里的 sigma 是噪声的标准差，0.1 * np.ones(env.action_space.shape) 表示标准差是 0.1，并且与动作空间的维度相同。这样每个维度的噪声标准差都是 0.1。

通过这种方式，动作中会加入一定的噪声，从而使得训练过程更加稳定，防止模型陷入局部最优解，增强探索性。

创建 DDPG 模型：

'MlpPolicy': 选择了多层感知器（MLP）作为策略网络的结构。该网络用于从状态中输出动作。

env: 环境对象，智能体将在该环境中进行训练。

policy_kwargs = dict(net_arch=[400, 300]): 这个参数定义了策略网络的结构，net_arch=[400, 300] 表示策略网络有两层隐藏层，分别有 400 个神经元和 300 个神经元。policy_kwargs 是传递给策略网络构造函数的附加参数。

verbose = 1: 这个参数设置了训练时的输出级别，verbose=1 表示打印训练过程中的信息。

tensorboard_log = "./ddpg_cartpole/": 这个参数指定了 TensorBoard 日志的存储路径，用于后期可视化训练过程。

action_noise=action_noise: 将前面创建的噪声对象 action_noise 传递给 DDPG 模型，用于在选择动作时加入噪声。

In [ ]:
# 步骤三：使用 DDPG 算法训练代理
from stable_baselines3 import DDPG
from stable_baselines3.common.vec_env import DummyVecEnv

# 将环境包装为向量环境
env = DummyVecEnv([lambda: gym.make('CartPoleSwingUp', render_mode='human')])

# 初始化 DDPG 代理
from stable_baselines3.common.noise import NormalActionNoise
# 加入噪声
action_noise = NormalActionNoise(mean = np.zeros(env.action_space.shape), sigm = 0.2 * np.ones(env.action_space.shape))
model = DDPG('MlpPolicy', env, policy_kwargs = dict(net_arch=[256, 128]), verbose = 1, learning_rate=0.01)

model.learn(total_timesteps = 10000000)

model.save("ddpg_cartpole_model")
# 评估训练后的模型

In [2]:
from stable_baselines3 import PPO
from stable_baselines3.common.vec_env import DummyVecEnv
import gym
import numpy as np

# 将环境包装为向量环境
# env = DummyVecEnv([lambda: gym.make('CartPoleSwingUp', render_mode='human')])

# 初始化 PPO 代理
model = PPO('MlpPolicy', env, policy_kwargs=dict(net_arch=[256, 128, 64]), verbose=1, learning_rate=0.001)

# 训练模型
model.learn(total_timesteps = 200000)

# 保存训练后的模型
model.save("ppo_cartpole_model")


Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
now Reset
-0.9999951377086175
-0.9999775969216879
-0.9999561174966157
-0.9999448243228184
-0.9998952283772958
-0.999773265336186
-0.9995428717801458
-0.9993034564642205
-0.9989502549723548
-0.9987687041248117
-0.9986387852961657
-0.9986386236271461
-0.9984695568963398
-0.9981253521435983
-0.9978379446956634
-0.9976203020037732
-0.997251300400198
-0.9966942304052089
-0.9964944861500169
-0.9966440474381546
-0.9970844711965128
-0.9972362113084793
-0.9976489168757116
-0.9980315647943904
-0.9982248842634253
-0.9982194985459107
-0.9983815403788937
-0.9984055318028973
-0.9984730227267733
-0.9985570357237317
-0.9985134099291568
-0.9986920022370965
-0.9990296559363717
-0.9992753299651367
-0.9995888664100393
-0.9998470235903574
-0.9999730580473941
-0.9999917857828817
-0.9999368147409228
-0.999766469464356
-0.9994714837778887
-0.9990735166911228
-0.9985715981410931
-0.9982229137614644
-0.9980371718194766

In [ ]:
from stable_baselines3 import SAC
from stable_baselines3.common.vec_env import DummyVecEnv
import gym
import numpy as np

# 将环境包装为向量环境

# 初始化 SAC 代理
model = SAC('MlpPolicy', env, policy_kwargs=dict(net_arch=[256, 128]), verbose=1, learning_rate=0.001)

# 训练模型
model.learn(total_timesteps=100000)

# 保存训练后的模型
model.save("sac_cartpole_model")


In [ ]:
from stable_baselines3 import TD3
from stable_baselines3.common.vec_env import DummyVecEnv
import gym
import numpy as np

# 初始化 TD3 代理
model = TD3('MlpPolicy', env, policy_kwargs=dict(net_arch=[256, 128]), verbose=1, learning_rate=0.001)

# 训练模型
model.learn(total_timesteps=100000)

# 保存训练后的模型
model.save("td3_cartpole_model")


In [ ]:
from stable_baselines3.common.evaluation import evaluate_policy

model = PPO.load("ppo_cartpole_model")
mean_reward, std_reward = evaluate_policy(model, env, n_eval_episodes = 10)
print(f"Mean reward: {mean_reward}, Std reward: {std_reward}")

# 测试模型
obs = env.reset()
done = False
while not done:
    action, _states = model.predict(obs, deterministic=True)
    obs, reward, done, info = env.step(action)
    env.render()  # 可视化环境

env.close()